In [1]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from scipy.spatial.distance import directed_hausdorff
from sklearn.svm import LinearSVC
from sklearn.metrics import confusion_matrix
import numpy as np
import datetime as dt
import pandas as pd

In [2]:
words = []
def train_to_sentence_form(path):
    # reads the file to a format of docs[doc[[sentence1],[sentence2]],...]
    docs=[]
    num_of_sentences = []
    with open(path) as f:
        line = f.readline()
        while line:
            line = line.rstrip('\n').split(" ")
            print(line)
            num = line.pop(0)
            number = int(num[1:-1])
            num_of_sentences.append(number)
            len_of_sentence = []

            for i,k in enumerate(line):
                if k.startswith('<'):
                    k=k[1:-1]
                    len_of_sentence.append(int(k))
                    line.pop(i)
            doc_sentence=[]       
            sentence=[]
            for j in len_of_sentence:
                sentence = line[:j]
                line=line[j:]
                docs.append( sentence) 
            line = f.readline()
    #print(len(docs))
    return docs,num_of_sentences     
    #docs is a list of lists where each list is a different sentence

In [3]:
vocabs = open("vocabs.txt").readlines()
for vocab in vocabs:
    word, _ = vocab.split(', ')
    words.append(word)

train_label = [i.strip() for i in open("train-label.dat").readlines()]
train_label = np.array(train_label)
path="train-data.dat"
docs,num_sentences = train_to_sentence_form(path)

['<2>', '<8>', '6705', '5997', '8310', '3606', '674', '8058', '5044', '4836', '<4>', '4312', '5154', '8310', '4225']
['<28>', '<4>', '1827', '1037', '8482', '483', '<9>', '3567', '6172', '6172', '2892', '1362', '787', '399', '777', '1332', '<8>', '318', '769', '4621', '3199', '1480', '6213', '971', '6890', '<4>', '5909', '15', '3445', '2475', '<4>', '324', '4138', '3404', '6176', '<4>', '65', '2926', '1375', '7705', '<3>', '709', '1323', '1652', '<4>', '5735', '7439', '3445', '2475', '<4>', '4396', '4382', '1798', '1870', '<3>', '1845', '4410', '7758', '<4>', '4278', '7775', '318', '769', '<5>', '2898', '1923', '8193', '2930', '485', '<3>', '5951', '6123', '2480', '<3>', '3158', '2193', '2438', '<4>', '7485', '3412', '5304', '5644', '<3>', '3734', '7459', '1652', '<5>', '3174', '8343', '426', '1968', '7506', '<4>', '561', '4051', '2722', '6717', '<3>', '6172', '3432', '7859', '<3>', '4595', '2351', '5951', '<5>', '135', '7023', '7215', '7038', '7221', '<4>', '560', '4631', '4411', '134

['<31>', '<4>', '681', '2615', '3521', '7798', '<5>', '6803', '645', '2420', '5411', '6819', '<8>', '470', '5359', '2650', '327', '5724', '6414', '5054', '3540', '<6>', '3031', '5307', '8518', '681', '4621', '2568', '<5>', '470', '6208', '4018', '1727', '6890', '<8>', '246', '6895', '1910', '1985', '3031', '1400', '4018', '7951', '<8>', '5542', '2411', '2011', '5354', '3100', '1749', '363', '7951', '<8>', '2480', '1749', '7382', '470', '5429', '3227', '135', '2461', '<5>', '2054', '3994', '1918', '2908', '2244', '<4>', '864', '1574', '7439', '1322', '<6>', '384', '5728', '3602', '704', '539', '315', '<6>', '413', '539', '5728', '1263', '4451', '1369', '<9>', '5724', '5728', '4477', '4176', '5728', '2094', '2083', '4731', '6890', '<7>', '2623', '7034', '3980', '3347', '2155', '5757', '2374', '<7>', '3544', '209', '5532', '1101', '672', '8126', '4772', '<6>', '406', '6933', '4504', '3606', '3839', '1752', '<7>', '1281', '2260', '1263', '1007', '2934', '2667', '4294', '<5>', '3491', '2260

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['<31>', '<8>', '3600', '7592', '1630', '4691', '126', '1319', '3683', '4552', '<4>', '6335', '3982', '6425', '3324', '<6>', '1049', '2804', '5523', '4679', '79', '815', '<6>', '1381', '1630', '1159', '2353', '674', '5793', '<8>', '4691', '3584', '952', '41', '1977', '550', '1720', '2368', '<7>', '6575', '2429', '1779', '379', '1281', '895', '7856', '<4>', '839', '2912', '452', '4252', '<5>', '839', '5528', '5556', '1977', '379', '<4>', '6039', '2015', '4958', '4688', '<9>', '1938', '4688', '4958', '5541', '839', '3952', '5961', '291', '2175', '<10>', '5961', '2093', '1558', '3400', '5382', '3400', '170', '1281', '5726', '674', '<8>', '8220', '185', '1630', '6575', '2429', '2780', '971', '568', '<6>', '3481', '6039', '5382', '2611', '5041', '1281', '<5>', '1781', '2206', '3584', '1985', '1281', '<7>', '5696', '1977', '1281', '4151', '7146', '8142', '3053', '<7>', '1977', '6958', '4151', '2964', '2743', '989', '6356', '<8>', '1757', '1254', '674', '1392', '3683', '1630', '4552', '3649',

In [4]:
#load and transform test data 
path2="test-data.dat"
docs_test,num_sentences_test = train_to_sentence_form(path2)
test_label = [i.strip() for i in open("test-label.dat").readlines()]
test_label = np.array(test_label)
data2 = []
for i in docs_test:
    final_L = ''
    for l in i:
        final_L = final_L + ' ' + words[int(l)]
    data2.append(final_L[1:])
print(len(data2))

['<31>', '<6>', '5282', '4641', '3031', '536', '5366', '1759', '<5>', '4855', '1037', '7752', '2287', '1090', '<7>', '1921', '6213', '3292', '5750', '6068', '5648', '1444', '<5>', '6157', '1574', '6955', '2287', '3816', '<9>', '5553', '568', '6955', '5523', '2793', '4312', '2033', '4217', '7593', '<3>', '6955', '965', '7553', '<7>', '7464', '2651', '8283', '1426', '5741', '4032', '740', '<8>', '470', '2413', '4767', '6629', '4551', '7859', '1007', '6629', '<6>', '945', '7553', '4551', '6955', '568', '7981', '<9>', '4386', '6166', '539', '8115', '6183', '7440', '1137', '6', '1137', '<6>', '4386', '6985', '470', '2151', '7340', '1779', '<6>', '4691', '1499', '4386', '4691', '8032', '1193', '<7>', '6955', '4124', '4386', '7553', '126', '7553', '4086', '<9>', '6955', '8235', '539', '4386', '965', '5598', '1921', '2904', '852', '<6>', '4691', '1137', '874', '323', '4691', '1574', '<5>', '482', '2651', '470', '5427', '6157', '<7>', '1783', '6073', '679', '7752', '3710', '561', '1072', '<6>',

['<2>', '<8>', '574', '4311', '2220', '2945', '3806', '574', '4334', '8500', '<8>', '354', '782', '2945', '2220', '1747', '7962', '6322', '4231']
['<19>', '<5>', '3375', '894', '1946', '3375', '3822', '<9>', '3291', '8356', '1598', '7962', '4312', '298', '5744', '298', '7409', '<9>', '894', '6768', '4432', '3654', '5169', '3994', '381', '6958', '3158', '<4>', '2110', '6249', '4755', '6174', '<6>', '6955', '7439', '2623', '7034', '1576', '384', '<7>', '389', '3375', '298', '5154', '5744', '298', '7409', '<5>', '8373', '1899', '4294', '5909', '5486', '<7>', '3617', '5669', '894', '965', '3375', '674', '1281', '<6>', '1145', '82', '6850', '6629', '3375', '384', '<4>', '7817', '1584', '2442', '6038', '<8>', '6890', '971', '3375', '298', '5154', '5744', '298', '7409', '<10>', '1366', '3726', '8406', '4311', '1758', '7719', '5055', '7649', '1904', '4858', '<8>', '3375', '1621', '3046', '815', '3087', '7649', '1904', '4858', '<5>', '1709', '446', '34', '371', '7593', '<5>', '7719', '1801', '5

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



73363


In [5]:
#apply CountVectorizer() and TfidfTransformer() to sentences
data = []
for i in docs:
    final_L = ''
    for l in i:
        final_L = final_L + ' ' + words[int(l)]
    data.append(final_L[1:])
print(data[:12])
print(len(data))   
count_vect = CountVectorizer()
X_train_counts = count_vect.fit_transform(data)
X_test_counts = count_vect.transform(data2)

print(X_train_counts.size)
tfidf_transformer = TfidfTransformer()
X_train_tfidf = tfidf_transformer.fit_transform(X_train_counts)
X_test_tfidf = tfidf_transformer.transform(X_test_counts)


['rubi rail helper demo more info auto complet', 'see new helper action', 'null length substr locat', 'exec messag messag pleas edit remov follow word content', 'roll stone com news song previou next page', 'good vibrat beach boy', 'smell teen spirit nirvana', 'want hold hand beatl', 'hound dog elvi', 'god know beach boy', 'walk line johnni cash', 'heaven led zeppelin']
149925
965852


In [6]:
#the vocabulary
train_vocabulary=count_vect.vocabulary_

In [7]:
#apply SVD keeping 20 components
from sklearn.decomposition import TruncatedSVD
svd = TruncatedSVD(n_components=20,n_iter=5, random_state=1)
mat_reduced = svd.fit_transform(X_train_tfidf)
Data_new = np.array(mat_reduced)
mat_reduced = svd.transform(X_test_tfidf)
Data_new_test = np.array(mat_reduced)

In [8]:
#modify the train bags with their instances
bags=[]
n=0
for i in num_sentences:
    bag1=[]
    for j in range(0,i):
        bag1.append(Data_new[n+j])
    bags.append(bag1)
    n=n+i

In [9]:
len(bags)

8251

#create distance matrix
start_time = dt.datetime.now()
dist=[]
#d=[]
for i in range (0,len(bags)):
    #start_time1 = dt.datetime.now()
    d=[]
    for j in range (0,len(bags)):
        d.append(max(directed_hausdorff(bags[i], bags[j])[0],directed_hausdorff(bags[j], bags[i])[0]))
    dist.append(d)
    #finish_time1 = dt.datetime.now()
    #time1 = finish_time1-start_time1 
    #print('the %d time is:', i, time1)
finish_time = dt.datetime.now()
time = finish_time-start_time 
print('the time is:', time)
# the time is: 5:30:23.234

dist = np.array(dist)
np.save('distance_matrix_test', dist)
#dist = np.load('distance_matrix')


In [10]:
#the fuction takes a distance Matrix and return (medoiods,clusters)
import random

def kMedoids(D, k, tmax=100):
    # determine dimensions of distance matrix D
    m, n = D.shape

    if k > n:
        raise Exception('too many medoids')

    # find a set of valid initial cluster medoid indices since we
    # can't seed different clusters with two points at the same location
    valid_medoid_inds = set(range(n))
    invalid_medoid_inds = set([])
    rs,cs = np.where(D==0)
    # the rows, cols must be shuffled because we will keep the first duplicate below
    index_shuf = list(range(len(rs)))
    np.random.shuffle(index_shuf)
    rs = rs[index_shuf]
    cs = cs[index_shuf]
    for r,c in zip(rs,cs):
        # if there are two points with a distance of 0...
        # keep the first one for cluster init
        if r < c and r not in invalid_medoid_inds:
            invalid_medoid_inds.add(c)
    valid_medoid_inds = list(valid_medoid_inds - invalid_medoid_inds)

    if k > len(valid_medoid_inds):
        raise Exception('too many medoids (after removing {} duplicate points)'.format(
            len(invalid_medoid_inds)))

    # randomly initialize an array of k medoid indices
    M = np.array(valid_medoid_inds)
    np.random.shuffle(M)
    M = np.sort(M[:k])

    # create a copy of the array of medoid indices
    Mnew = np.copy(M)

    # initialize a dictionary to represent clusters
    C = {}
    for t in range(tmax):
        # determine clusters, i. e. arrays of data indices
        J = np.argmin(D[:,M], axis=1)
        for kappa in range(k):
            C[kappa] = np.where(J==kappa)[0]
        # update cluster medoids
        for kappa in range(k):
            J = np.mean(D[np.ix_(C[kappa],C[kappa])],axis=1)
            j = np.argmin(J)
            Mnew[kappa] = C[kappa][j]
        np.sort(Mnew)
        # check for convergence
        if np.array_equal(M, Mnew):
            break
        M = np.copy(Mnew)
    else:
        # final update of cluster memberships
        J = np.argmin(D[:,M], axis=1)
        for kappa in range(k):
            C[kappa] = np.where(J==kappa)[0]

    # return results
    return M, C

#select medoids
med,cl = kMedoids(dist, 20)

In [43]:
medo = np.array(med)
np.save('medoids_train', medo)

In [10]:
med = np.load("medoids_train.npy")

In [11]:
#create a dataframe with zeros
number_of_clusters = 20
initform = np.zeros([train_label.size,number_of_clusters])
dfmed = pd.DataFrame(initform,columns=["Cluster "+ str(i) for i in range(number_of_clusters)])


In [12]:
#find the Hausdorff distance between every bag and medoids to create the features vectors
for i in range(0,train_label.size):
    for j in range(0,number_of_clusters):
        dfmed.iloc[i][j] = max(directed_hausdorff(bags[i], bags[med[j]])[0],directed_hausdorff(bags[med[j]], bags[i])[0])
    

In [13]:
#the final data
dfmed.head()

Cluster 0  Cluster 1  Cluster 2  Cluster 3  Cluster 4  Cluster 5  \
0   0.414548   0.401836   0.426836   0.411074   0.836155   0.544826   
1   0.372133   0.328745   0.368366   0.374088   0.760516   0.490156   
2   0.419354   0.413711   0.399528   0.423316   0.759667   0.488866   
3   0.233521   0.344603   0.373293   0.185321   0.700270   0.524134   
4   0.388933   0.371395   0.367590   0.433855   0.694607   0.490917   

   Cluster 6  Cluster 7  Cluster 8  Cluster 9  Cluster 10  Cluster 11  \
0   0.407771   0.408575   0.579547   0.944473    0.579162    0.391801   
1   0.372669   0.238157   0.641974   0.850228    0.533825    0.307718   
2   0.330713   0.396701   0.599053   0.858785    0.532925    0.411040   
3   0.376851   0.319734   0.631277   0.814152    0.548552    0.308023   
4   0.403075   0.410760   0.596351   0.799618    0.544618    0.259998   

   Cluster 12  Cluster 13  Cluster 14  Cluster 15  Cluster 16  Cluster 17  \
0    0.955807    0.412778    0.570592    0.427822    0.433890    0.831481   
1    0.934594    0.364070    0.653746    0.366005    0.371403    0.431278   
2    0.742596    0.424959    0.596838    0.336061    0.325223    0.605831   
3    0.841190    0.307854    0.646235    0.301611    0.388868    0.835004   
4    0.934694    0.416376    0.594559    0.377108    0.410364    0.798560   

   Cluster 18  Cluster 19  
0    0.334216    0.536428  
1    0.362992    0.490171  
2    0.321356    0.496524  
3    0.285463    0.511169  
4    0.413026    0.501732

#save the data as csv file
dfmed.to_csv("train_kmedoids__.csv")

In [22]:
#modify the test bags their instances
bags_test=[]
n=0
for i in num_sentences_test:
    bag1t=[]
    for j in range(0,i):
        bag1t.append(Data_new_test[n+j])
    bags_test.append(bag1t)
    n=n+i

In [23]:
len(bags_test)

3983

In [24]:
#create a dataframe with zeros for test data
number_of_clusters = 20
initform = np.zeros([test_label.size,number_of_clusters])
dfmed_test = pd.DataFrame(initform,columns=["Cluster "+ str(i) for i in range(number_of_clusters)])

In [25]:
dfmed_test.shape

(3983, 20)

In [26]:
#find the Hausdorff distance between every bag_test of test data and medoids (of train) to create the features vectors
for i in range(0,test_label.size):
    for j in range(0, number_of_clusters):
        dfmed_test.iloc[i][j] = max(directed_hausdorff(bags_test[i], bags[med[j]])[0],directed_hausdorff(bags[med[j]], bags_test[i])[0])
    

#save test data
dfmed_test.to_csv("test_kmedoids__.csv")

In [28]:
dfmed_test.head()

Cluster 0  Cluster 1  Cluster 2  Cluster 3  Cluster 4  Cluster 5  \
0   0.565573   0.547392   0.495616   0.562451   0.703978   0.502939   
1   0.469409   0.401623   0.333249   0.476613   0.805703   0.342119   
2   0.384557   0.312924   0.389292   0.411835   0.672799   0.466394   
3   0.473452   0.466551   0.401149   0.464564   0.791047   0.513305   
4   0.808575   0.753974   0.706795   0.797602   0.359352   0.732952   

   Cluster 6  Cluster 7  Cluster 8  Cluster 9  Cluster 10  Cluster 11  \
0   0.461356   0.533346   0.511473   0.812625    0.483915    0.535096   
1   0.432360   0.461758   0.433043   0.918064    0.466054    0.445373   
2   0.409785   0.382691   0.577415   0.796995    0.535203    0.368254   
3   0.459288   0.471535   0.606052   0.919412    0.504188    0.454072   
4   0.805603   0.805271   0.680269   0.308018    0.543955    0.719199   

   Cluster 12  Cluster 13  Cluster 14  Cluster 15  Cluster 16  Cluster 17  \
0    0.789981    0.569305    0.555282    0.481415    0.455797    0.754616   
1    0.855148    0.469964    0.451244    0.422415    0.450098    0.795665   
2    0.916947    0.402691    0.560840    0.409079    0.402178    0.741018   
3    0.831151    0.467442    0.616263    0.479776    0.501343    0.800062   
4    0.936394    0.686095    0.807068    0.580584    0.716676    0.803696   

   Cluster 18  Cluster 19  
0    0.469166    0.607302  
1    0.381937    0.575796  
2    0.413112    0.499199  
3    0.447599    0.533876  
4    0.806966    0.847615

In [11]:
#to load the data use
import pandas as pd
DataTrain = pd.read_csv("train_kmedoids.csv") 
DataTest = pd.read_csv("test_kmedoids.csv")

In [12]:
DataTrain.head(5)

Cluster 0  Cluster 1  Cluster 2  Cluster 3  Cluster 4  Cluster 5  \
0        0.0        0.0        0.0        0.0        0.0        0.0   
1        0.0        0.0        0.0        0.0        0.0        0.0   
2        0.0        0.0        0.0        0.0        0.0        0.0   
3        0.0        0.0        0.0        0.0        0.0        0.0   
4        0.0        0.0        0.0        0.0        0.0        0.0   

   Cluster 6  Cluster 7  Cluster 8  Cluster 9  Cluster 10  Cluster 11  \
0        0.0        0.0        0.0        0.0         0.0         0.0   
1        0.0        0.0        0.0        0.0         0.0         0.0   
2        0.0        0.0        0.0        0.0         0.0         0.0   
3        0.0        0.0        0.0        0.0         0.0         0.0   
4        0.0        0.0        0.0        0.0         0.0         0.0   

   Cluster 12  Cluster 13  Cluster 14  Cluster 15  Cluster 16  Cluster 17  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   Cluster 18  Cluster 19  
0         0.0         0.0  
1         0.0         0.0  
2         0.0         0.0  
3         0.0         0.0  
4         0.0         0.0